<a href="https://colab.research.google.com/github/CrAvila/LandElevated/blob/main/Subject_Property_Valuation_V1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
import pandas as pd
import numpy as np
import folium
from folium.plugins import HeatMap
from sklearn.preprocessing import StandardScaler, PolynomialFeatures
from sklearn.linear_model import LinearRegression, Ridge, Lasso
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor
from sklearn.model_selection import LeaveOneOut, cross_val_score
from sklearn.svm import SVR
from sklearn.neural_network import MLPRegressor
from datetime import datetime
from scipy import stats
import warnings
from geopy.distance import great_circle
from folium.plugins import MeasureControl
import warnings

# Suppress warnings
warnings.filterwarnings("ignore", category=UserWarning, module='sklearn')

# Load the dataset
df = pd.read_csv('comps_extended.csv')

# Keep the APN column separately for identification
apn_column = df['APN']

# Remove unnecessary columns (excluding APN)
columns_to_delete = ["State", "County", "Water", "Electricity", "List Date", "Access",
                     "Days on Market", "Google Map Link", "Google Earth Link", "Redfin Link",
                     "Zillow Link", "Subdivision", "Zoning", "PID", "Land Use"]
df.drop(columns=columns_to_delete, inplace=True, errors='ignore')
df.dropna(inplace=True)

# Correct date format
def correct_date_format(date_str):
    if isinstance(date_str, str) and "-" in date_str:
        day, month_abbr, year = date_str.split('-')
        month_dict = {'Jan': '01', 'Feb': '02', 'Mar': '03', 'Apr': '04', 'May': '05', 'Jun': '06',
                      'Jul': '07', 'Aug': '08', 'Sep': '09', 'Oct': '10', 'Nov': '11', 'Dec': '12'}
        month = month_dict.get(month_abbr, month_abbr)
        return f"{month}/{day}/{year}"
    else:
        return date_str

df['Sale Date'] = df['Sale Date'].apply(correct_date_format)
df['Sale Date'] = pd.to_datetime(df['Sale Date'], format='mixed')
df['Sale Price'] = df['Sale Price'].str.replace('[\$,]', '', regex=True).astype(float)
df['Date'] = (df['Sale Date'] - df['Sale Date'].min()).dt.days

# Calculate z-scores for all features
df_zscore = df.select_dtypes(include=['number']).apply(stats.zscore)
df_zscore_loc = df[["Latitude",	"Longitude"]]

# Set a threshold for outlier detection (e.g., 3 standard deviations)
threshold = 3

# Identify outliers
outliers = (df_zscore.abs() > threshold).any(axis=1)

# Remove outliers from the original DataFrame
df = df[~outliers]

# Reset the index and update the original DataFrame
df = df.reset_index(drop=True)

# Calculate pairwise distances and find the medoid
def calculate_total_distance(index, points):
    medoid_point = points.iloc[index]
    total_distance = points.apply(lambda row: great_circle((row['Latitude'], row['Longitude']), (medoid_point['Latitude'], medoid_point['Longitude'])).miles, axis=1).sum()
    return total_distance

points = df[['Latitude', 'Longitude']]
total_distances = points.apply(lambda row: calculate_total_distance(row.name, points), axis=1)
medoid_idx = total_distances.idxmin()
medoid = df.iloc[medoid_idx][['Latitude', 'Longitude']]

# Function to calculate distance in miles
def calculate_distance(row, medoid):
    return great_circle((row['Latitude'], row['Longitude']), (medoid['Latitude'], medoid['Longitude'])).miles

# Calculate distance of each property from the medoid
df['Distance_from_Medoid'] = df.apply(calculate_distance, axis=1, medoid=medoid)

# Filter properties that are within miles from the medoid
df = df[df['Distance_from_Medoid'] <= 10]

# Reset index again after filtering
df = df.reset_index(drop=True)

# Separate features and target variable
X = df.drop(columns=["Sale Price", "Sale Date", "APN", "Distance_from_Medoid"])
y = df["Sale Price"]

# Standardize the features
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X)

# Calculate the mean sale price for relative metrics
mean_sale_price = np.mean(y)

# Define models to evaluate
models = {
    "Linear Regression": LinearRegression(),
    "Ridge Regression": Ridge(),
    "Lasso Regression": Lasso(),
    "Decision Tree Regression": DecisionTreeRegressor(),
    "Random Forest Regression": RandomForestRegressor(),
    "Gradient Boosting Regression": GradientBoostingRegressor(),
    "Support Vector Regression": SVR(kernel='rbf', C=10, gamma=0.1, epsilon=0.01),
    "Neural Network": MLPRegressor(hidden_layer_sizes=(20, 20, 15, 10, 10, 10), activation='relu', solver='adam', alpha=0.001, learning_rate='adaptive', max_iter=1000)
}

# Add Polynomial Regression with degree tuning
best_degree = None
best_rmse = float('inf')
loo = LeaveOneOut()
for degree in range(1, 10):
    poly = PolynomialFeatures(degree)
    X_poly = poly.fit_transform(X_scaled)
    poly_model = LinearRegression()
    scores = -cross_val_score(poly_model, X_poly, y, cv=loo, scoring='neg_mean_squared_error')
    rmse_scores = np.sqrt(scores)
    mean_rmse = rmse_scores.mean()
    if mean_rmse < best_rmse:
        best_rmse = mean_rmse
        best_degree = degree

# Train the best polynomial regression model on the entire dataset
poly = PolynomialFeatures(best_degree)
X_poly_best = poly.fit_transform(X_scaled)
best_poly_model = LinearRegression().fit(X_poly_best, y)

# Add the best polynomial model to the list
models[f"Polynomial Regression (degree {best_degree})"] = best_poly_model

# Evaluate models using LOOCV
results = {}
for name, model in models.items():
    if "Polynomial" in name:
        scores = -cross_val_score(best_poly_model, X_poly_best, y, cv=loo, scoring='neg_mean_squared_error')
    else:
        scores = -cross_val_score(model, X_scaled, y, cv=loo, scoring='neg_mean_squared_error')
    rmse_scores = np.sqrt(scores)
    mean_rmse = rmse_scores.mean()
    results[name] = mean_rmse
    relative_rmse = (mean_rmse / mean_sale_price) * 100
    print(f"{name}: RMSE = {mean_rmse} ({relative_rmse:.2f}% of mean sale price)")

# Select the best model
best_model_name = min(results, key=results.get)
best_model = models[best_model_name]
relative_rmse_best = (results[best_model_name] / mean_sale_price) * 100
print(f"\nBest Model: {best_model_name} with RMSE = {results[best_model_name]} ({relative_rmse_best:.2f}% of mean sale price) \n")

# Train the best model on the entire dataset
if "Polynomial" in best_model_name:
    best_model.fit(X_poly_best, y)
else:
    best_model.fit(X_scaled, y)

# Predict price ranges for 1 acre and July 31, 2024
end_of_month_date = datetime(2024, 7, 31)
end_of_month_difference = (end_of_month_date - df['Sale Date'].min()).days

lat_min, lat_max = df['Latitude'].min(), df['Latitude'].max()
lon_min, lon_max = df['Longitude'].min(), df['Longitude'].max()

lat_grid, lon_grid = np.meshgrid(
    np.linspace(lat_min, lat_max, 300),
    np.linspace(lon_min, lon_max, 300)
)

grid_points = np.c_[lat_grid.ravel(), lon_grid.ravel()]
fixed_acreage = 1.0

# Prepare the input for prediction for the end of the month
grid_input = np.c_[
    np.full(grid_points.shape[0], fixed_acreage),
    grid_points,
    np.full(grid_points.shape[0], end_of_month_difference)
]

# Standardize the grid input
grid_input_scaled = scaler.transform(grid_input)

# Generate polynomial features for the grid input if the best model is polynomial
if "Polynomial" in best_model_name:
    grid_input_poly = poly.transform(grid_input_scaled)
    predicted_prices = best_model.predict(grid_input_poly)
else:
    predicted_prices = best_model.predict(grid_input_scaled)

# Ensure non-negative predictions
predicted_prices = np.maximum(predicted_prices, 0)

# Prepare data for the heatmap
heatmap_data = np.c_[grid_points, predicted_prices]

# Create a folium map centered around the mean latitude and longitude
map_center = [df['Latitude'].mean(), df['Longitude'].mean()]
mymap = folium.Map(location=map_center, zoom_start=12)
mymap.add_child(MeasureControl(primary_length_unit='kilometers', secondary_length_unit='miles'))

# Add the heatmap to the map
heatmap = HeatMap(
    data=[[row[0], row[1], row[2]] for row in heatmap_data],
    min_opacity=0.1,
    max_zoom=18,
    radius=15,
    blur=15,
    gradient={0.4: 'blue', 0.65: 'lime', 1: 'red'}
)
mymap.add_child(heatmap)

# Add markers for actual data points using real dates for predictions
X_scaled_actual = scaler.transform(df[['Acreage', 'Latitude', 'Longitude', 'Date']])

if "Polynomial" in best_model_name:
    X_poly_actual = poly.transform(X_scaled_actual)
    predicted_prices_actual = best_model.predict(X_poly_actual)
else:
    predicted_prices_actual = best_model.predict(X_scaled_actual)

# Ensure non-negative predictions for actual data points
predicted_prices_actual = np.maximum(predicted_prices_actual, 0)

# Predict prices for the end of the current month
end_of_month_input = np.c_[
    df['Acreage'],
    df['Latitude'],
    df['Longitude'],
    np.full(df.shape[0], end_of_month_difference)
]
end_of_month_input_scaled = scaler.transform(end_of_month_input)

if "Polynomial" in best_model_name:
    end_of_month_input_poly = poly.transform(end_of_month_input_scaled)
    predicted_end_of_month_prices = best_model.predict(end_of_month_input_poly)
else:
    predicted_end_of_month_prices = best_model.predict(end_of_month_input_scaled)

# Ensure non-negative predictions for end of month
predicted_end_of_month_prices = np.maximum(predicted_end_of_month_prices, 0)

# Include the APN in the DataFrame
df['APN'] = apn_column.apply(lambda x: str(int(round(x))) if not pd.isnull(x) else 'Unknown')

# Keep only the latest entry for each APN
df_latest = df.sort_values('Sale Date').drop_duplicates('APN', keep='last')

for i, row in df_latest.iterrows():
    popup_content = (
        f"<b>APN: </b> {row['APN']} <br>"
        f"<b>Acreage: </b> {row['Acreage']} <br>"
        f"<b>Latitude: </b> {row['Latitude']} <br>"
        f"<b>Longitude: </b> {row['Longitude']} <br>"
        f"<br>"
        f"<b>Real Price:</b> ${row['Sale Price']:.2f}<br>"
        f"<b>Predicted Price ({str(row['Sale Date']).split(' ')[0]}):</b> ${predicted_prices_actual[i]:.2f}<br>"
        f"<b>Predicted Price (July 31, 2024):</b> ${predicted_end_of_month_prices[i]:.2f}"
    )
    popup = folium.Popup(popup_content, max_width=300)
    folium.Marker(
        location=[row['Latitude'], row['Longitude']],
        popup=popup
    ).add_to(mymap)

# Save the predicted values in the DataFrame
df['Predicted Price'] = predicted_prices_actual
df['PEoM Price'] = predicted_end_of_month_prices

# Print the data points with their real and predicted values
display(df[['APN', 'Acreage', 'Latitude', 'Longitude', 'Date', 'Sale Price', 'Predicted Price', 'PEoM Price']])

# Function to estimate price of a subject property and add it to the map
def estimate_and_add_to_map(acreage, latitude, longitude, sale_date, apn):
    # Convert the sale date to days from the minimum sale date in the dataset
    sale_date = pd.to_datetime(sale_date)
    date_difference = (sale_date - df['Sale Date'].min()).days

    # Prepare the input for prediction
    subject_input = np.array([[acreage, latitude, longitude, date_difference]])
    subject_input_scaled = scaler.transform(subject_input)

    if "Polynomial" in best_model_name:
        subject_input_poly = poly.transform(subject_input_scaled)
        predicted_price = best_model.predict(subject_input_poly)
    else:
        predicted_price = best_model.predict(subject_input_scaled)

    # Ensure non-negative prediction
    predicted_price = np.maximum(predicted_price, 0)

    # Add the subject property to the map
    popup_content = (
        f"<b>APN: </b> {apn} <br>"
        f"<b>Acreage: </b> {acreage} <br>"
        f"<b>Latitude: </b> {latitude} <br>"
        f"<b>Longitude: </b> {longitude} <br>"
        f"<b>Predicted Price:</b> ${predicted_price[0]:.2f}"
    )
    popup = folium.Popup(popup_content, max_width=300)
    folium.Marker(
        location=[latitude, longitude],
        popup=popup,
        icon=folium.Icon(color='orange')
    ).add_to(mymap)

    return predicted_price[0]

# Example usage of the function
subject_property = {
    "apn": "2055020053",
    "acreage": 0.46,
    "latitude": 34.152905,
    "longitude": -118.741977,
    "sale_date": "2024-07-31"
}

estimated_price = estimate_and_add_to_map(**subject_property)
print(f"\nEstimated Price for the subject property: ${estimated_price:.2f}\n")

# Save the map with the subject property marker to an HTML file
mymap.save("predicted_prices_heatmap_with_subject_property.html")

mymap

Linear Regression: RMSE = 263539.94086495327 (45.55% of mean sale price)
Ridge Regression: RMSE = 262389.0487104198 (45.35% of mean sale price)
Lasso Regression: RMSE = 263540.1232988154 (45.55% of mean sale price)
Decision Tree Regression: RMSE = 121520.83333333333 (21.00% of mean sale price)
Random Forest Regression: RMSE = 116667.08333333333 (20.16% of mean sale price)
Gradient Boosting Regression: RMSE = 134678.11236301507 (23.28% of mean sale price)
Support Vector Regression: RMSE = 421337.0850836374 (72.82% of mean sale price)
Neural Network: RMSE = 154927.76275404936 (26.78% of mean sale price)
Polynomial Regression (degree 1): RMSE = 263539.9408649534 (45.55% of mean sale price)

Best Model: Random Forest Regression with RMSE = 116667.08333333333 (20.16% of mean sale price) 



APN  Acreage   Latitude   Longitude   Date  Sale Price  \
0   2061018067     0.33  34.138410 -118.743137  16569     40000.0   
1   2061018067     0.33  34.138410 -118.743137   9624     90000.0   
2   2061018067     0.33  34.138410 -118.743137   9518     35000.0   
3   2061018067     0.33  34.138410 -118.743137   7523     22500.0   
4   2061025054     0.54  34.141653 -118.747642  16520    195000.0   
5   2055029005     1.72  34.167185 -118.740157  16334   1600000.0   
6   2055029005     1.72  34.167185 -118.740157  15922   1600000.0   
7   2055029005     1.72  34.167185 -118.740157  15908   1600000.0   
8   2055029005     1.72  34.167185 -118.740157  13096   1350000.0   
9   3091017018     1.54  34.156536 -118.735634  15134    470000.0   
10  2055023065     1.54  34.156536 -118.735634   9903    560000.0   
11  2055023065     1.54  34.156536 -118.735634   3743    220000.0   
12  2055023065     0.18  34.138941 -118.743687  15915    185000.0   
13  2061018062     2.04  34.139564 -118.741438  15897    200000.0   
14  2061017057     0.26  34.129214 -118.634230  15951    170000.0   
15  2080015052     0.26  34.129214 -118.634230  15932    170000.0   
16  2080015052     2.33  34.129214 -118.634230  15938    299000.0   
17  2055021039     1.37  34.166614 -118.739638  16447   1499000.0   
18  2055029004     1.37  34.166614 -118.739638  15057   1100000.0   
19  2055029004     0.82  34.150882 -118.744190  15071    400000.0   
20  2055017051     0.98  34.153242 -118.744952  15533    430000.0   
21  2055019037     0.98  34.153242 -118.744952  13809    425000.0   
22  2055019037     0.20  34.167848 -118.748481  15232    380000.0   
23  2050013022     0.20  34.167848 -118.748481  14364    845000.0   

    Predicted Price  PEoM Price  
0           91215.0    116125.0  
1           77975.0    116125.0  
2           60375.0    116125.0  
3           42250.0    116125.0  
4          162090.0    172400.0  
5         1571690.0   1300000.0  
6         1574720.0   1300000.0  
7         1574720.0   1300000.0  
8         1300000.0   1300000.0  
9          459990.0    460390.0  
10         496440.0    460390.0  
11         322250.0    460390.0  
12         158675.0    163525.0  
13         284500.0    288370.0  
14         164885.0    171595.0  
15         165035.0    171595.0  
16         326870.0    328960.0  
17        1409890.0   1167510.0  
18        1178590.0   1167510.0  
19         412400.0    411650.0  
20         424150.0    422250.0  
21         422250.0    422250.0  
22         614240.0    778250.0  
23         767300.0    778250.0


Estimated Price for the subject property: $295200.00

